# Creating Supplementary Figure 1 to Compare Imputations
The purpose of this Jupyter Notebook is to compare the raw filtered data with the imputed data from SAVER, scImpute, and MAGIC.

### Part 0: Importing Packges

In [1]:
# import statements
import magic
import scprep
import csv

import numpy as np
import pandas as pd
import matplotlib
import matplotlib.pyplot as plt
%matplotlib inline

from sklearn.decomposition import PCA
from sklearn.manifold import TSNE
from scprep.io.csv import load_csv

### Part 1: Loading in Data

In [8]:
# load raw filtered data
dat = load_csv('../../data/filtered_data/HIV1_Bld.csv')

In [3]:
# load scimpute data (preprocessed with R script)
scimpute_dat = load_csv('../../data/imputation_intermediate/different_imputations/scimpute_hiv1.csv')
scimpute_dat = scimpute_dat.transpose()

In [4]:
# load SAVER data (preprocessed with R script)
saver_dat = load_csv('../../data/imputation_intermediate/different_imputations/saver_hiv1.csv')
saver_dat = saver_dat.transpose()

In [9]:
# compute MAGIC here, so we have magic_op to do PCA with
magic_op = magic.MAGIC()

# compute MAGIC PCA
dat_magic=magic_op.fit_transform(dat)

      Calculating MAGIC...
      Running MAGIC on 1669 cells and 22935 genes.
      Calculating graph and diffusion operator...
      Calculating PCA...


/Library/Frameworks/Python.framework/Versions/3.7/lib/python3.7/site-packages/magic/magic.py:376: UserWarning: Input matrix contains unexpressed genes. Please remove them prior to running MAGIC.
  warnings.warn("Input matrix contains unexpressed genes. "


      Calculated PCA in 2.94 seconds.
      Calculating KNN search...
      Calculated KNN search in 0.33 seconds.
      Calculating affinities...
    Calculated affinities in 0.34 seconds.
  Calculated graph and diffusion operator in 3.81 seconds.
  Calculating imputation...
    Automatically selected t = 13
  Calculated imputation in 0.38 seconds.
Calculated MAGIC in 5.26 seconds.


### Part 2: PCA on Raw and Imputed Matrices

In [14]:
# confirm all four matrices are the same shape
print(dat.shape)
print(scimpute_dat.shape)
print(saver_dat.shape)
print(dat_magic.shape)

(1669, 22935)
(1669, 22935)
(1669, 22935)
(1669, 22935)


In [15]:
# compute raw PCA
dat_pca = PCA().fit_transform(np.array(dat))

In [16]:
# compute scimpute PCA
scimpute_pca = PCA().fit_transform(np.array(scimpute_dat))

In [17]:
# compute SAVER PCA
saver_pca = PCA().fit_transform(np.array(saver_dat))

In [33]:
# get color map for raw matrix
cd14_dat = dat.loc[:, 'CD14']
cd14_dat_list = np.array(cd14_dat.values.tolist())
cd14_dat_list = np.reshape(cd14_dat_list, [1669, 1])
dat_col = np.transpose(cd14_dat_list)

# get color map for scimpute matrix
cd14_scimpute = scimpute_dat.loc[:, 'CD14']
cd14_scimpute_list = np.array(cd14_scimpute.values.tolist())
cd14_scimpute_list = np.reshape(cd14_scimpute_list, [1669, 1])
scimpute_col = np.transpose(cd14_scimpute_list)

# get color map for saver matrix
cd14 = saver_dat.iloc[:,3240]

# get color map for magic matrix
cd14_magic = dat_magic.loc[:, 'CD14']
cd14_magic_list = np.array(cd14_magic.values.tolist())
cd14_magic_list = np.reshape(cd14_magic_list, [1669, 1])
magic_col = np.transpose(cd14_magic_list)

In [36]:
# plot comparison
fig, (ax1, ax2, ax3, ax4) = plt.subplots(4,1, figsize=(8, 24), dpi=800)

scprep.plot.scatter2d(dat_pca, c=dat_col, 
                      label_prefix="PC", title='PCA on Raw Data',
                      legend_title="CD14", ax=ax1, ticks=False)

scprep.plot.scatter2d(scimpute_pca, c=scimpute_col,
                      label_prefix="PC", title='PCA with scImpute',
                      legend_title="CD14", ax=ax2, ticks=False)

scprep.plot.scatter2d(saver_pca, c=cd14,
                      label_prefix="PC", title='PCA with SAVER',
                      legend_title="CD14", ax=ax3, ticks=False)

scprep.plot.scatter2d(dat_magic, c=magic_col, 
                      label_prefix="PC", title='PCA with MAGIC',
                      legend_title="CD14", ax=ax4, ticks=False)

plt.savefig('../../output/figures/supp_figure_1_comparison_imputation_A_PCA.png')
plt.show()

### Part 3: t-SNE on Raw and Imputed Matrices

In [37]:
# magic t-sne
tSNE_magic=TSNE(n_components=2).fit_transform(dat_magic)

In [38]:
# raw t-sne
tSNE_dat=TSNE(n_components=2).fit_transform(dat)

In [39]:
# scimpute t-sne
tSNE_scimpute=TSNE(n_components=2).fit_transform(scimpute_dat)

In [40]:
# saver t-sne
tSNE_saver=TSNE(n_components=2).fit_transform(saver_dat)

In [41]:
# plot comparison
fig, (ax1, ax2, ax3, ax4) = plt.subplots(4,1, figsize=(8, 24), dpi=800)

scprep.plot.scatter2d(tSNE_dat, c=dat_col, 
                      label_prefix="tSNE", title='tSNE on Raw Data',
                      legend_title="CD14", ax=ax1, ticks=False)

scprep.plot.scatter2d(tSNE_scimpute, c=scimpute_col, 
                      label_prefix="tSNE", title='tSNE with scImpute',
                      legend_title="CD14", ax=ax2, ticks=False)

scprep.plot.scatter2d(tSNE_saver, c=cd14, 
                      label_prefix="tSNE", title='tSNE with SAVER',
                      legend_title="CD14", ax=ax3, ticks=False)

scprep.plot.scatter2d(tSNE_magic, c=magic_col, 
                      label_prefix="tSNE", title='tSNE with MAGIC',
                      legend_title="CD14", ax=ax4, ticks=False)

plt.savefig('../../output/figures/supp_figure_1_comparison_imputation_B_tsne.png')
plt.show()